In [1]:
import meshutil
import stl.mesh
import numpy
import trimesh

In [2]:
b1 = numpy.array([
    [0, 0, 0],
    [1, 0, 0],
    [1, 1, 0],
    [0, 1, 0],
], dtype=numpy.float64) - 0.5
b2 = numpy.array(b1 + [0,0,1])

In [7]:
ang = 0.15
xform = meshutil.Transform().translate(0,0,0.5)

mesh = meshutil.join_boundary_simple(b1, b2)
for i,bound in enumerate(meshutil.subdivide_boundary(b2)):
    m = xform.apply_to(bound) #xform.rotate([0,0,1], i*numpy.pi/2).apply_to(bound)
    mesh = mesh.concat(meshutil.join_boundary_simple(bound, m))

# One problem: without an actual transform in subdivide_boundary,
# the transforms aren't inherited, and there is no transformed space.
# I'm just dealing directly with transformed geometry.
#
# My rotation around z in the loop above won't work the way I intended.
#
# In other words: I don't need to subdivide *geometry*.
# I need to subdivide *space* and then put geometry in it.

mesh.to_stl_mesh().save("simple.stl")

In [65]:
mesh_fname = "cube_test.stl"

# center at (0,0,0) for sanity reasons
center = meshutil.Transform().translate(-0.5, -0.5, -0.5)
base = meshutil.cube(open_xz=False).transform(center)

xform = center.translate(-0.5,1.5,-0.5).scale(0.5)
ang = 0.15
l2 = meshutil.cube_distort(ang, open_xz=False)

mesh = base
for layer in range(2):
    for i in range(4):
        m = l2.transform(xform.rotate([0,1,0], i*numpy.pi/2))
        mesh = mesh.concat(m)
    xform = xform.rotate([-1,0,1], ang).scale(1.0).translate(0, 0.7, 0)

# Work around some annoying-ass trimesh/threejs bug:
wtf = meshutil.Transform().scale(0.1).translate(5,0,0)
base = base.transform(wtf)
mesh = mesh.concat(base)
mesh.to_stl_mesh().save(mesh_fname)

In [66]:
# TODO: Just use the mesh data directly (no sense in saving & re-loading)
m = trimesh.load_mesh(mesh_fname)
#m.show()
scene = trimesh.Scene([m])
# Seems to do nothing:
# scene.camera_transform = scene.camera.look_at(m.vertices, distance=10)
scene.show()

face_normals didn't match triangles, ignoring!


In [4]:
scene.camera_transform

array([[ 1.        ,  0.        ,  0.        , -0.07059288],
       [ 0.        ,  1.        ,  0.        ,  0.09608653],
       [-0.        ,  0.        ,  1.        ,  2.14795328],
       [ 0.        ,  0.        ,  0.        ,  1.        ]])